## Preambule

In [1]:
# General packages
import numpy as np
import pandas as pd
from tqdm import tqdm
from pathlib import Path
import xarray as xr
import json

# Plotting
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from plotly.colors import n_colors

## Parameter

In [2]:
params = dict(start_year_analysis=2021)

## Paths

In [3]:
path_main = Path("K:/Code/EffortSharing/")
path_data = Path("K:/Data/Data_EffortSharing/DataUpdate_ongoing/")
path_figs = path_main / "Figures" / "ECEMF_paper"

## Read data files

In [4]:
xr_dataread = xr.open_dataset(path_data / "xr_dataread.nc")
all_regions_iso = np.load(path_data / "all_regions.npy")
all_regions_names = np.load(path_data / "all_regions_names.npy")
all_countries_iso = np.load(path_data / "all_countries.npy", allow_pickle=True)
all_countries_names = np.load(path_data / "all_countries_names.npy", allow_pickle=True)

In [5]:
df = pd.read_excel(Path("X:/user/dekkerm/Data/") / "UNFCCC_Parties_Groups_noeu.xlsx", sheet_name = "Country groups")
countries_iso2 = np.array(df["Country ISO Code"])
group_ldc = countries_iso2[np.array(df["LDC"]) == 1]
group_hdc = countries_iso2[np.array(df["HICO"]) == 1]

In [6]:
df = pd.read_excel("X:/user/dekkerm/Data/UNFCCC_Parties_Groups_noeu.xlsx", sheet_name = "Country groups")
countries_iso = np.array(df["Country ISO Code"])
group_cvf = countries_iso[np.array(df["CVF (24/10/22)"]) == 1]
group_g20 = countries_iso[np.array(df["G20"]) == 1]
group_eu = countries_iso[np.array(df["EU"]) == 1]
group_g7 = countries_iso[np.array(df["G7"]) == 1]
group_na = countries_iso[np.array(df["Northern America"]) == 1]
group_um = countries_iso[np.array(df["Umbrella"]) == 1]
group_au = countries_iso[np.array(df["Australasia"]) == 1]
group_af = countries_iso[np.array(df["African Group"]) == 1]
group_sids = countries_iso[np.array(df["SIDS"]) == 1]
xr_alloc_2030 = xr.open_dataset(path_data / "xr_alloc_2030.nc")
xr_alloc_2040 = xr.open_dataset(path_data / "xr_alloc_2040.nc")
group_ldc = countries_iso[np.array(df["LDC"]) == 1]
group_eg = countries_iso[np.array(df["European Group"]) == 1]

In [7]:
traj_15 = xr.open_dataset(path_data / "xr_traj_t16_r50.nc")
xr_alloc_2030 = xr.open_dataset(path_data / "xr_alloc_2030.nc")
xr_alloc_2040 = xr.open_dataset(path_data / "xr_alloc_2040.nc")

xr_alloc_2030 = xr_alloc_2030.drop_vars(['PCB']).rename({'PCB_lin': 'PCB'})
xr_alloc_2040 = xr_alloc_2040.drop_vars(['PCB']).rename({'PCB_lin': 'PCB'})
traj_15 = traj_15.drop_vars(['PCB']).rename({'PCB_lin': 'PCB'})

In [8]:
xr_allocs = {}
for cty in ['EU', 'USA', 'IND', 'CHN', 'JPN', 'AUS', 'BRA', 'RUS', 'ZAF']:
    xr_allocs[cty] = xr.open_dataset(path_data / "Allocations" / ("xr_alloc_"+cty+".nc"))

2030 alloc Berg

In [9]:
df_berg = pd.read_excel(Path("X:/user/dekkerm/Data/") / "Berg_paper" / "Berg2019_data.xlsx", sheet_name = "Emission pathways")
df_berg2 = df_berg[(df_berg.Scenario == 'Gt400') & (df_berg.Category == 'Emissions|Kyoto Gases') & (df_berg.Year == 2030)].drop(columns=['Scenario', 'Fixed variable', 'Category', 'Year', 'Unnamed: 10',  'Unnamed: 12', 'Region #'])
df_berg2 = df_berg2.rename({'Sensitivity case': "Parameters"}, axis=1)
approaches = np.array(df_berg2.Approach)
approaches[approaches == 'IEPC'] = 'PC'
df_berg2['Approach'] = approaches
df_berg2 = df_berg2.melt(id_vars=["Approach", "Region", "Parameters"], var_name="Range", value_name="Value")
df_berg2 = df_berg2.set_index(['Approach', "Region", "Parameters", "Range"])
xr_berg = df_berg2.to_xarray()

Yann

In [10]:
df_rob = pd.read_excel(Path("X:/user/dekkerm/Data/") / "Robiou_paper" / "Robiou2016_15data.xlsx", sheet_name = "1.5°C National allocations")
df_rob2 = df_rob.drop(columns=['Country names', 'INDC Low assessment', 'INDC average assessment', 'INDC High assessment', 2025, '2025.1', 2030, '2030.1', 2040, '2040.1', 2050, '2050.1', 'Peaking year', 'First net-zero allocation year', 'Budget 2010-2050'])
df_rob2 = df_rob2.rename({'Country code ISO Alpha-3': 'Region', "approaches names": "Approach", 'Budget 2010-2100': "Budget_2010"}, axis=1)
approaches = np.array(df_rob2.Approach)
approaches[approaches == 'CER'] = 'GF'
approaches[approaches == 'EPC'] = 'PCC'
approaches[approaches == 'CAP'] = 'AP'
approaches[approaches == 'CPC'] = 'ECPC'
df_rob2['Approach'] = approaches
df_rob2 = df_rob2.set_index(['Approach', 'Region'])
xr_rob = df_rob2.to_xarray()

Find out high/medium/low income

In [11]:
group_mdc = []
for reg in all_countries_iso:
    if reg not in group_hdc and reg not in group_ldc:
        group_mdc.append(reg)

## Default settings

In [12]:
settings_global = {'Temperature': 1.6,
                   'Risk': 0.5,
                   'NegEmis': 0.5,
                   'NonCO2red': 0.5,
                   'Timing': "Immediate"}
settings_globalt = {'Risk': 0.50,
                   'NegEmis': 0.5,
                   'NonCO2red': 0.5,
                   'Timing': "Immediate"}
settings_globaltraj = {'NegEmis': 0.5,
                   'NonCO2red': 0.5,
                   'Timing': "Immediate"}
settings_params = {'Convergence_year': 2050,
                   'Scenario': 'SSP2',
                   'Discount_factor': 0,
                   'Historical_startyear': 1950,
                   'Capability_threshold': "Th",
                   'RCI_weight': "Half"}
alloc_dimensions = ['Scenario', 'Convergence_year', 'Discount_factor', 'Historical_startyear', 'Capability_threshold', 'RCI_weight']

rules = ['GF', 'PC', 'PCC', 'PCB', 'AP', 'ECPC', 'GDR']
rulecolors = ['sienna', 'purple', 'goldenrod', 'mediumvioletred', 'forestgreen', 'tomato', 'steelblue']
rulenames = ['Grandfathering', '(Immediate) per capita', 'Per capita convergence', 'Per capita via budget', 'Ability to pay', 'Equal Cumulative per capita', 'Greenhouse Development Rights']
rules_short = ['PCC', 'AP', 'ECPC']
rulecols_short = ['goldenrod', 'forestgreen', 'tomato']

## Plot

In [13]:
lw = 4
risk = 0.5
time_hist = np.arange(1990, params['start_year_analysis']+1)
time_fut = np.arange(params['start_year_analysis'], 2101)
whichtemps = [1.5, 1.6, 1.8, 2.0]

In [14]:
cols_ctys = np.array(rulecols_short)[np.array(xr_alloc_2030.sel(Temperature=1.6, **settings_globalt, **settings_params)[rules_short].to_array()).argmax(axis=0)]

Traces for panel (a)

In [15]:
traces_panel_a = []

# Historical emissions
traces_panel_a.append(go.Scatter(x=time_hist,
                                 y=xr_dataread.sel(Time=time_hist, Region='EARTH').GHG_hist/1e3,
                                 name='Historical emissions',
                                 line={'color': 'black', 'width': lw}, mode='lines', legend='legend1', showlegend=True))

# Baseline emissions
for var_i in range(3):
    var = [xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region='EARTH').GHG_base.min(dim='Scenario'),
           xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region='EARTH').GHG_base.max(dim='Scenario'),
           xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region='EARTH').GHG_base.mean(dim='Scenario')][var_i]
    traces_panel_a.append(go.Scatter(x=time_fut,
                                    y=var/1e3,
                                    name='Baseline emissions',
                                    legend='legend1', 
                                    fill = [None, 'tonexty', None][var_i],
                                    line={'color': 'grey', 'width': [0, 0, lw][var_i]}, mode='lines',
                                    showlegend=[False, False, True][var_i]))

# Global emissions pathways
for temp_i, temp in enumerate(whichtemps):
       col = plt.cm.coolwarm(0.25+temp_i/len(whichtemps))
       col2 = plt.cm.coolwarm(0.05+temp_i/len(whichtemps))
       for var_i in range(2):
              var = [xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Temperature=temp, Risk=[0.33, 0.5 , 0.67]).GHG_globe.min(dim=['NegEmis', 'NonCO2red', 'Timing', 'Risk']),
                     xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Temperature=temp, Risk=[0.33, 0.5 , 0.67]).GHG_globe.max(dim=['NegEmis', 'NonCO2red', 'Timing', 'Risk']),
                     xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Temperature=temp, **settings_globalt).GHG_globe][var_i]
              traces_panel_a.append(go.Scatter(x=time_fut,
                                                 y=var/1e3,
                                                 name="Global "+str(temp)+"&deg;C (50%)",
                                                 fill = [None, 'tonexty', None][var_i],
                                                 legend='legend1',
                                                 fillcolor='rgba('+str(col[0])+','+str(col[1])+','+str(col[2])+', 0.15)',
                                                 line={'color': 'rgba('+str(col2[0])+','+str(col2[1])+','+str(col2[2])+', 0.15)', 'width': [0, 0, lw][var_i]}, mode='lines',
                                                 showlegend=[False, False, False][var_i]))
for temp_i, temp in enumerate(whichtemps):
       col = plt.cm.coolwarm(0.25+temp_i/len(whichtemps))
       col2 = plt.cm.coolwarm(0.25+temp_i/len(whichtemps))
       var_i = 2
       var = [xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Temperature=temp, Risk=[0.33, 0.5 , 0.67]).GHG_globe.min(dim=['NegEmis', 'NonCO2red', 'Timing', 'Risk']),
              xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Temperature=temp, Risk=[0.33, 0.5 , 0.67]).GHG_globe.min(dim=['NegEmis', 'NonCO2red', 'Timing', 'Risk']),
              xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Temperature=temp, **settings_globalt).GHG_globe][var_i]
       traces_panel_a.append(go.Scatter(x=time_fut,
                                          y=var/1e3,
                                          name="Global "+str(temp)+"&deg;C (50%)",
                                          fill = [None, 'tonexty', None][var_i],
                                          legend='legend1',
                                          line={'color': 'rgb('+str(col2[0])+','+str(col2[1])+','+str(col2[2])+')', 'width': [0, 0, lw][var_i]}, mode='lines',
                                          showlegend=True))

Traces for panel (b)

In [16]:
traces_panel_b = []
for cty_i, cty in enumerate(np.array(xr_alloc_2040.Region)):
    pop = float(xr_dataread.Population.sel(Scenario='SSP2', Region=cty, Time=params['start_year_analysis']))
    if not np.isnan(pop):
        if pop > 1e-1:
            if cty in all_countries_iso:
                popn = np.sqrt(pop / np.nanmax(xr_dataread.Population.sel(Scenario='SSP2', Region=all_countries_iso, Time=params['start_year_analysis'])))
                traces_panel_b.append(go.Scatter(x=[xr_dataread.GDP.sel(Scenario='SSP2', Region=cty, Time=params['start_year_analysis'])*1e9/pop/1e6],
                                        y=[xr_dataread.GHG_hist.sel(Time=np.arange(1950, params['start_year_analysis']), Region=cty).sum(dim='Time')/pop/1e6*1e3],
                                        mode='markers+text',
                                        text=cty,
                                        textfont={'size': popn * 32+3, 'color': 'black'},
                                        marker={'size': popn * 60+8, 'color': cols_ctys[cty_i], 'opacity': 0.7},
                                        showlegend=False))

Traces for panels (c)-(h)

In [17]:
traces_panels_ch = []
for cty_i, cty in enumerate(['USA', 'EU', 'IND', 'CHN', 'ZAF', 'BRA']):
    emis_2021 = float(xr_dataread.GHG_hist.sel(Time=2021, Region=cty)/1e3)
    traces_panel_i = []
    traces_panel_j = []

    # Historical emissions
    traces_panel_i.append(go.Scatter(x=np.arange(1990, params['start_year_analysis']+1),
                                     y=xr_dataread.sel(Time=np.arange(1990, params['start_year_analysis']+1), Region=cty).GHG_hist/1e3/emis_2021,
                                     name='Historical emissions', line={'color': 'black', 'width': lw}, mode='lines', showlegend=False))

    # Baseline emissions
    for var_i in range(3):
        var = [xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty).GHG_base.min(dim='Scenario'),
                xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty).GHG_base.max(dim='Scenario'),
                xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty).GHG_base.mean(dim='Scenario')][var_i]
        traces_panel_i.append(go.Scatter(x=time_fut,
                                        y=var/1e3/emis_2021,
                                        fill = [None, 'tonexty', None][var_i],
                                        line={'color': 'grey', 'width': [0, 0, lw][var_i]}, mode='lines',
                                        showlegend=False))
    vals = np.array(xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty).GHG_base.sel(Time=2030))
    vals_default = float(xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty, Scenario='SSP2').GHG_base.sel(Time=2030))
    traces_panel_j.append(go.Violin(x=['Base']*len(vals),
                                    y=vals/1e3/emis_2021,
                                    showlegend=False,
                                    width=1.5,
                                    points=False,
                                    line={'width': 0},
                                    line_color='grey')
                )
    traces_panel_j.append(go.Scatter(x=['Base'],
                                    y=[vals_default/1e3/emis_2021],
                                    mode='markers',
                                    showlegend=False,
                                    marker_symbol = 'diamond-wide',
                                    marker=dict(size=15),
                                    line={'width': 2},
                                    line_color='grey')
                )

    if cty == 'USA': sl = True
    else: sl = False

    # NDC
    vals = [np.nanmin(np.array(xr_dataread.sel(Region=cty).GHG_ndc)), np.nanmax(np.array(xr_dataread.sel(Region=cty).GHG_ndc))]
    traces_panel_i.append(go.Scatter(x=[2030, 2030],
                                    y=np.array(vals)/1e3/emis_2021,
                                    name = 'NDC',
                                    line={'color': 'black', 'width': lw*2}, mode='lines+markers',
                                    legend='legend2',
                                    showlegend=sl))
    traces_panel_j.append(go.Scatter(x=['NDC', 'NDC'],
                                    y=np.array(vals)/1e3/emis_2021,
                                    line={'color': 'black', 'width': lw*2}, mode='lines+markers',
                                    showlegend=False))

    # Allocation
    trajs = [traj_15.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty, **settings_globaltraj).min(dim=alloc_dimensions),
                traj_15.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty, **settings_globaltraj).max(dim=alloc_dimensions),
                traj_15.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty, **settings_globaltraj).median(dim=alloc_dimensions)]
    for alloc_i, alloc in enumerate(rules):
        for var_i in range(2):
            var = trajs[var_i][alloc]
            traces_panel_i.append(go.Scatter(x=time_fut,
                                            y=var/1e3/emis_2021,
                                            fill = [None, 'tonexty', None][var_i],
                                            line={'color': rulecolors[alloc_i], 'width': [0, 0, lw][var_i]}, mode='lines',
                                            showlegend=False))
        vals = np.array(traj_15.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty).sel(Time=2030)[alloc]).flatten()
        traces_panel_j.append(go.Violin(x=[alloc]*len(vals),
                                        y=vals/1e3/emis_2021,
                                    legend='legend2',
                                        showlegend=sl,
                                        width=1.5,
                                        name=rulenames[alloc_i],
                                        points=False,
                                        line={'width': 0},
                                        line_color=rulecolors[alloc_i])
                    )
                    
    # NDC
    vals = [np.nanmin(np.array(xr_dataread.sel(Region=cty).GHG_ndc)), np.nanmax(np.array(xr_dataread.sel(Region=cty).GHG_ndc))]
    traces_panel_i.append(go.Scatter(x=[2030, 2030],
                                    y=np.array(vals)/1e3/emis_2021,
                                    line={'color': 'black', 'width': lw*2}, mode='lines+markers',
                                    showlegend=False))
    traces_panel_j.append(go.Scatter(x=['NDC', 'NDC'],
                                    y=np.array(vals)/1e3/emis_2021,
                                    line={'color': 'black', 'width': lw*2}, mode='lines+markers',
                                    showlegend=False))
    
    traces_panels_ch.append([traces_panel_i, traces_panel_j])

traces_panels_ch_2 = []
for cty_i, cty in enumerate(['USA', 'EU', 'IND', 'CHN', 'ZAF', 'BRA']):
    emis_2021 = float(xr_dataread.GHG_hist.sel(Time=2021, Region=cty)/1e3)
    traces_panel_i = []
    traces_panel_j = []
    # Allocation
    trajs = traj_15.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty, **settings_globaltraj).median(dim=alloc_dimensions)
    for alloc_i, alloc in enumerate(rules):
        trajs2 = float(traj_15.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty).sel(Time=2030, **settings_globaltraj, **settings_params)[alloc])
        var = trajs[alloc]
        traces_panel_i.append(go.Scatter(x=time_fut,
                                        y=var/1e3/emis_2021,
                                        fill = None,
                                        line={'color': rulecolors[alloc_i], 'width': lw}, mode='lines',
                                        showlegend=False))
        traces_panel_j.append(go.Scatter(x=[alloc],
                                        y=[trajs2/1e3/emis_2021],
                                        mode='markers',
                                        marker_symbol = 'diamond-wide',
                                        showlegend=False,
                                        marker=dict(size=15),
                                        line={'width': 2},
                                        line_color=rulecolors[alloc_i])
                    )
    
    traces_panels_ch_2.append([traces_panel_i, traces_panel_j])

Full plot

In [18]:
# df_ar6_raw = pd.read_csv("X:/user/dekkerm/Data/IPCC/AR6_Scenarios_Database_World_v1.1.csv")
# df_ar6 = df_ar6_raw[df_ar6_raw.Variable.isin(['Emissions|Kyoto Gases'])]
# df_ar6 = df_ar6.reset_index(drop=True)
  
# df_ar6_meta = pd.read_excel("X:/user/dekkerm/Data/IPCC/AR6_Scenarios_Database_metadata_indicators_v1.1.xlsx", sheet_name='meta_Ch3vetted_withclimate')
# mods = np.array(df_ar6_meta.Model)
# scens = np.array(df_ar6_meta.Scenario)
# modscens_meta = np.array([mods[i]+'|'+scens[i] for i in range(len(scens))])
# df_ar6_meta['ModelScenario'] = modscens_meta
# df_ar6_meta = df_ar6_meta[['ModelScenario', 'Category', 'Policy_category']]
# df_ar6_meta = df_ar6_meta[df_ar6_meta.Category.isin(['C1', 'C2'])]
# df_ar6_meta = df_ar6_meta.reset_index(drop=True)
# ms_meta_refined = np.array(df_ar6_meta.ModelScenario)

# mods = np.array(df_ar6.Model)
# scens = np.array(df_ar6.Scenario)
# modscens = np.array([mods[i]+'|'+scens[i] for i in range(len(scens))])
# df_ar6['ModelScenario'] = modscens
# df_ar6 = df_ar6.drop(['Model', 'Scenario', 'Unit', 'Region'], axis=1)
# df_ar6_c1 = df_ar6[df_ar6.ModelScenario.isin(np.array(ms_meta_refined))]

In [19]:
# dummy = df_ar6_c1.melt(id_vars=["Variable", "ModelScenario"], var_name="Time", value_name="Value")
# dummy['Time'] = np.array(dummy['Time'].astype(int))
# dummy = dummy.set_index(["Variable", "ModelScenario", "Time"])
# xr_scen = xr.Dataset.from_dataframe(dummy)
# xr_scen = xr_scen.reindex(Time = np.arange(1990, 2101))
# xr_scen_c1 = xr_scen.interpolate_na(dim="Time", method="linear")

# startpoint = xr_dataread.sel(Time=2021, Region="EARTH").GHG_hist
# kyoto2021 = xr_scen_c1.sel(Time=2021)/1e3
# offsets = (startpoint/1e3-kyoto2021)
# ar6_corr = xr_scen_c1.sel(Time=np.arange(2021, 2101))/1e3 + offsets

# compensation_form = np.array([1]*80)#np.array(list(np.linspace(0, 1, len(np.arange(2021, 2050))))+[1]*len(np.arange(2050, 2101)))
# ms = ar6_corr.ModelScenario[np.where(np.abs(ar6_corr.sel(Variable='Emissions|Kyoto Gases', Time=np.arange(2021, 2101)).sum(dim='Time').Value*1e3 - float(xr_dataread.GHG_globe.sel(NegEmis=0.5, NonCO2red=0.5, Timing='Immediate', Temperature=1.5, Risk=0.5, Time=np.arange(2021, 2101)).sum(dim='Time'))) < 75000)[0]]

# ar6_filtered = ar6_corr.sel(ModelScenario=ms)

In [20]:
ghg_2015 = float(xr_dataread.sel(Region='EARTH', Time=2015).GHG_hist)/1e3
ghg_base = float(xr_dataread.sel(Region='EARTH', Time=2040).GHG_base.mean(dim='Scenario'))/1e3

In [21]:
fig = make_subplots(rows=4, cols=6,
                    specs=[[{'colspan': 4, 'rowspan': 2}, {}, {}, {}, {'colspan': 2, 'rowspan': 2}, {}],
                           [{}, {}, {}, {}, {}, {}],
                           [{}, {}, {}, {}, {}, {}],
                           [{}, {}, {}, {}, {}, {}]],
                    horizontal_spacing = 0.02, vertical_spacing=0.06)

# Panel (a)
for t_i, t in enumerate(traces_panel_a):
     fig.add_trace(t, 1, 1)
fig.add_trace(go.Scatter(x=[1990, 2100], y=[0, 0], line={'color': 'black', 'width': lw/2, 'dash': 'dash'}, mode='lines', showlegend=False), 1, 1)
fig.add_trace(go.Scatter(x=[2040, 2040], y=[-10, 73], line={'color': 'black', 'width': lw/2, 'dash': 'dash'}, mode='lines', showlegend=False), 1, 1)
fig.add_trace(go.Scatter(x=[2015, 2015], y=[52.47, 57], line={'color': 'black', 'width': lw/2}, mode='lines', showlegend=False), 1, 1)
#fig.add_trace(go.Scatter(x=2015, y=55, text='2015', showarrow=False, mode='text', font=dict(color='black', size=16)), 1, 1)

fig.add_trace(go.Scatter(x=[2015], y=[58], text='<b>2015</b>: '+str(np.round(float(xr_dataread.GHG_hist.sel(Region='EARTH', Time=2015))/1e3, 1))+' Gt CO<sub>2</sub>e', mode='text', textfont=dict(color='black', size=18), showlegend=False), 1, 1)
fig.add_trace(go.Scatter(x=[2040], y=[76], text='<b>2040</b>', mode='text', textfont=dict(color='black', size=18), showlegend=False), 1, 1)
fig.add_trace(go.Scatter(x=[2041], y=[ghg_base], text='                          <b>Baseline</b>: +'+str(np.round((ghg_base - ghg_2015)/ghg_2015*100,1))+'%', mode='text', textfont=dict(color='black', size=18), showlegend=False), 1, 1)
for temp_i, temp in enumerate(whichtemps):
       vari = float(xr_dataread.sel(Time=2040, Temperature=temp, **settings_globalt).GHG_globe/1e3)
       var = (ghg_2015-vari)/ghg_2015
       fig.add_trace(go.Scatter(x=[2041], y=[vari], text='                <b>'+str(temp)+'</b>: -'+str(np.round(var*100,1))+'%', mode='text', textfont=dict(color='black', size=18), showlegend=False), 1, 1)


# Panel (b)
for t_i, t in enumerate(traces_panel_b):
     fig.add_trace(t, 1, 5)
  
# Panel (c)-(h)
for a_i, a in enumerate(traces_panels_ch):
     for b_i, traces in enumerate(a):
          for t_i, t in enumerate(traces):
               fig.add_trace(t, [3, 4][b_i], [1, 2, 3, 4, 5, 6][a_i])
for a_i, a in enumerate(traces_panels_ch_2):
     for b_i, traces in enumerate(a):
          for t_i, t in enumerate(traces):
               fig.add_trace(t, [3, 4][b_i], [1, 2, 3, 4, 5, 6][a_i])
# for a_i, a in enumerate(traces_panels_ch_2):
#      for t_i, t in enumerate(a):
#           fig.add_trace(t, 3, [1, 2, 3, 4, 5, 6][a_i])
#           #fig.add_trace(t[1], 4, [1, 2, 3, 4, 5, 6][a_i])

for col in range(1, 7):
     fig.add_trace(go.Scatter(x=[1990, 2100], y=[0, 0], line={'color': 'black', 'width': lw/3, 'dash': 'dash'}, mode='lines', showlegend=False), 3, col)
     fig.add_trace(go.Scatter(x=['Base', 'GDR'], y=[0, 0], line={'color': 'black', 'width': lw/3, 'dash': 'dash'}, mode='lines', showlegend=False), 4, col)

for row_i, row in enumerate([3, 4]):
     for col in [1, 2, 3, 4, 5, 6]:
          if col == 1: fig.update_yaxes(row=row, col=col, range=[[-1, -0.6][row_i], [3, 1.6][row_i]])
          else: fig.update_yaxes(row=row, col=col, visible=False, range=[[-1, -0.6][row_i], [3, 1.6][row_i]])

fs = 25
fig.update_xaxes(title_text="GDP per capita in 2021 [USD]", type="log", row=1, col=5, range=[2.4, 5])
fig.update_yaxes(type="log", row=1, col=5, range=[-1.8, 0.5])
fig.update_yaxes(title_text="Global GHG emissions including LULUCF [Gt CO<sub>2</sub>e/yr]", row=1, col=1, range=[-10, 90], title_font_size=18)
fig['layout'].update(
    annotations=[dict(x=0.01, y=1.0, text='<b>(a) Global GHG emission trajectories</b>', xref='paper', yref='paper', showarrow=False, font=dict(color='black', size=fs)),
                 dict(x=0.69, y=1.0, text='<b>(b) Highest allocations</b>', xref='paper', yref='paper', xanchor='left', showarrow=False, font=dict(color='black', size=fs)),
                 dict(x=0.69, y=0.97, text='out of PCC, AP and ECPC, 2030 in 1.6&deg;C pathway', xref='paper', yref='paper', xanchor='left', showarrow=False, font=dict(color='black', size=fs*0.7)),
                 dict(x=0.71, y=0.94, text='GHG emissions 1950-2021 per capita [kt CO<sub>2</sub>e]', xref='paper', yref='paper', showarrow=False, textangle=-90, font=dict(color='black',  size=18)),

                 dict(x=0.005, y=0.44, text='<b>(c) United<br>States</b>', xref='paper', yref='paper', showarrow=False, font=dict(color='black', size=fs)),
                 dict(x=0.16, y=0.44, text='<b>(d) European<br>Union</b>', xref='paper', yref='paper', showarrow=False, font=dict(color='black', size=fs)),
                 dict(x=0.38, y=0.46, text='<b>(e) India</b>', xref='paper', yref='paper', showarrow=False, font=dict(color='black', size=fs)),
                 dict(x=0.55, y=0.46, text='<b>(f) China</b>', xref='paper', yref='paper', showarrow=False, font=dict(color='black', size=fs)),
                 dict(x=0.83, y=0.46, text='<b>(g) South-Africa</b>', xref='paper', yref='paper', showarrow=False, font=dict(color='black', size=fs)),
                 dict(x=0.94, y=0.46, text='<b>(h) Brazil</b>', xref='paper', yref='paper', showarrow=False, font=dict(color='black', size=fs)),
                 dict(x=-0.05, y=-0.04, text='GHG emissions allocations compared to 2021 levels (1.6&deg;C, 50%)', xref='paper', yref='paper', textangle=-90, showarrow=False, font=dict(color='black', size=fs*0.7)),
                 dict(x=-0.035, y=0.36, text='Over time', xref='paper', yref='paper', textangle=-90, showarrow=False, font=dict(color='black', size=fs*0.7)),
                 dict(x=-0.035, y=0.08, text='In 2030', xref='paper', yref='paper', textangle=-90, showarrow=False, font=dict(color='black', size=fs*0.7)),
])

fig.update_yaxes(ticks="inside")
fig.update_xaxes(ticks="inside")
fig.update_layout(height=1300, width=1600, template='simple_white')
fig.update_layout(legend1=dict(
    yanchor="top",
    y=0.74,
    xanchor="left",
    #orientation="h",
    x=0.01,
    font=dict( 
        size=16,
        color="black"
    ),
), legend2=dict(
    yanchor="top",
    y=-0.05,
    xanchor="left",
    orientation="h",
    x=0.03,
    font=dict( 
        size=16,
        color="black"
    ),
),
    font=dict(
        size=16,
    ))

In [22]:
# def html_w(typ):
#     return '<html> '+typ+' <p style="font-family: Arial">'

# with open('K:/Code/EffortSharing/Figures/Paper_FairShares/Figure_1.html', 'a') as f:
#     f.write(html_w('<h1>')+'Indicators</p></h1>')
#     f.write(fig.to_html(full_html=False, include_plotlyjs='cdn'))

In [23]:
import kaleido

In [28]:
fig.write_image("K:/Code/EffortSharing/Figures/Paper_FairShares/Figure_1.png", scale=3, engine='kaleido')